In [173]:
import pandas as pd
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import matplotlib.colors as mcolors

import os
import re
import math

In [66]:
def load_all_runs(folder_path):
    """
    Reads all CSV files in folder_path and returns a DataFrame with
    MultiIndex: [dimension, seed, method] and column 'loss_function'.
    """
    records = []

    # Regex pattern to parse filenames: method_seed_dimension.csv
    pattern = re.compile(r"(?P<method>\w+)_(?P<seed>\d+)_(?P<dimension>\d+)\.csv")

    for filename in os.listdir(folder_path):
        match = pattern.match(filename)
        if match:
            info = match.groupdict()
            method = info["method"]
            seed = int(info["seed"])
            dimension = int(info["dimension"])

            # Read CSV
            df = pd.read_csv(os.path.join(folder_path, filename))
            # Assuming 'loss_function' column exists
            for i, val in enumerate(df["loss_function"]):
                records.append({
                    "dimension": dimension,
                    "seed": seed,
                    "method": method,
                    "iteration": i,
                    "loss_function": val
                })

    combined_df = pd.DataFrame.from_records(records)
    # Optional: set multiindex
    combined_df.set_index(["dimension", "seed", "method", "iteration"], inplace=True)
    return combined_df

In [67]:
def summarize_runs(df):
    """
    Input: DataFrame with MultiIndex [dimension, seed, method, iteration]
    Output: DataFrame with columns: dimension, method, iteration, mean, std
    """
    # Reset index for easier grouping
    df_reset = df.reset_index()

    # TODO this is not broken beacuse iteration is the key one here
    #   - figure out why the shading did not work
    #   - maybe plot the runs within the region to see what is happening
    summary_df = (
        df_reset
        .groupby(["dimension", "method", "iteration"])["loss_function"]
        .agg(["mean", "std"])
        .reset_index()
    )
    return summary_df

In [284]:
def with_alpha(color_name, alpha=0.2):
    # Convert a named color like "red" or "blue" into rgba
    rgb = mcolors.to_rgb(color_name)  # (r,g,b) in 0-1
    r, g, b = [int(255 * x) for x in rgb]
    return f'rgba({r},{g},{b},{alpha})'


# def plot_summary_facet(summary_df, title):
#     # Consistent colors for methods
#     method_colors = {
#         "brownian": "blue",
#         "hadamard": "red"
#     }
#
#     dimensions = sorted(summary_df["dimension"].unique())
#     n_dims = len(dimensions)
#
#     # Compute rows and cols for near-square layout
#     n_cols = math.ceil(math.sqrt(n_dims))
#     n_rows = math.ceil(n_dims / n_cols)
#
#     fig = make_subplots(
#         rows=n_rows, cols=n_cols,
#         subplot_titles=[f"Dimension {d}" for d in dimensions],
#         shared_xaxes=False,
#         shared_yaxes=False
#     )
#
#     # Map each dimension index to (row, col)
#     pos_map = {d: (i // n_cols + 1, i % n_cols + 1) for i, d in enumerate(dimensions)}
#
#     for d in dimensions:
#         row, col = pos_map[d]
#         df_dim = summary_df[summary_df["dimension"] == d]
#
#         for method in df_dim["method"].unique():
#             df_m = df_dim[df_dim["method"] == method]
#             color = method_colors.get(method, "black")
#
#             # Mean line
#             fig.add_trace(go.Scatter(
#                 x=df_m["iteration"],
#                 y=df_m["mean"],
#                 mode="lines",
#                 name=method,
#                 line=dict(color=color, width=2),
#                 showlegend=bool(d == dimensions[0])  # only show legend once
#             ), row=row, col=col)
#
#             # Shaded ±1 SD
#             fig.add_trace(go.Scatter(
#                 x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
#                 y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
#                 fill="toself",
#                 fillcolor=with_alpha(color, 0.2),
#                 line=dict(color="rgba(255,255,255,0)"),
#                 showlegend=False,
#                 hoverinfo="skip"
#             ), row=row, col=col)
#
#     # Update axes for all subplots
#     for i in range(1, n_rows + 1):
#         for j in range(1, n_cols + 1):
#             fig.update_xaxes(showticklabels=True, row=i, col=j, title_text="Iteration")
#             fig.update_yaxes(showticklabels=True, row=i, col=j, title_text="Loss", type="log")
#
#     fig.update_layout(
#         title=title,
#         height=400 * n_rows,
#         width=400 * n_cols,
#     )
#
#     fig.show()

def plot_summary_facet(summary_df, title, dimension_order=None):
    # Consistent colors for methods
    method_colors = {
        "brownian": "blue",
        "hadamard": "red"
    }

    # Case 1: dimension_order is provided
    if dimension_order is not None:
        # allow either flat list or list of lists
        if isinstance(dimension_order[0], (list, tuple)):
            layout = dimension_order
        else:
            layout = [dimension_order]  # single row

        n_rows = len(layout)
        n_cols = max(len(row) for row in layout)
        dimensions = [d for row in layout for d in row if d in summary_df["dimension"].unique()]

        # Map each dimension to (row, col) based on layout
        pos_map = {}
        for i, row in enumerate(layout, start=1):
            for j, d in enumerate(row, start=1):
                if d in dimensions:
                    pos_map[d] = (i, j)

    # Case 2: default near-square layout
    else:
        dimensions = sorted(summary_df["dimension"].unique())
        n_dims = len(dimensions)
        n_cols = math.ceil(math.sqrt(n_dims))
        n_rows = math.ceil(n_dims / n_cols)
        pos_map = {d: (i // n_cols + 1, i % n_cols + 1) for i, d in enumerate(dimensions)}

    # Build subplot grid
    fig = make_subplots(
        rows=n_rows,
        cols=n_cols,
        subplot_titles=[f"d = {d}" for d in dimensions],
        shared_xaxes=False,
        shared_yaxes=False,
        horizontal_spacing=0.1,  # default is 0.02 → more spacing
        vertical_spacing=0.2
    )

    # Plot data
    for d in dimensions:
        row, col = pos_map[d]
        df_dim = summary_df[summary_df["dimension"] == d]

        for method in df_dim["method"].unique():
            df_m = df_dim[df_dim["method"] == method]
            color = method_colors.get(method, "black")

            # Mean line
            fig.add_trace(
                go.Scatter(
                    x=df_m["iteration"],
                    y=df_m["mean"],
                    mode="lines",
                    name=method.title(),
                    line=dict(color=color, width=2),
                    showlegend=bool(d == dimensions[0])  # only show legend once
                ),
                row=row, col=col
            )

            # Shaded ±1 SD
            fig.add_trace(
                go.Scatter(
                    x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
                    y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
                    fill="toself",
                    fillcolor=with_alpha(color, 0.2),
                    line=dict(color="rgba(255,255,255,0)"),
                    showlegend=False,
                    hoverinfo="skip"
                ),
                row=row, col=col
            )

    # Update axes
    for i in range(1, n_rows + 1):
        for j in range(1, n_cols + 1):
            fig.update_xaxes(showticklabels=True, row=i, col=j, title_text="Iteration")
            fig.update_yaxes(showticklabels=True, row=i, col=j, title_text="Loss", type="log", tickformat=".0e")

    fig.update_layout(
        title=title,
        height=300 * n_rows,
        width=350 * n_cols,
    )

    fig.show()



In [291]:
folder = "../log_allencahn"
all_runs = load_all_runs(folder)
allen_summary = summarize_runs(all_runs)
plot_summary_facet(summary, "Allen-Cahn Example")

In [292]:
folder = "../log_hjb"
all_runs = load_all_runs(folder)
hjb_summary = summarize_runs(all_runs)
# plot_summary_facet(summary, "Hamilton-Jacobi-Bellman Example", dimension_order=[[2, 4], [16, 128]])
# plot_summary_facet(summary, "Hamilton-Jacobi-Bellman Example", dimension_order=[[1, 5], [15, 100]])
plot_summary_facet(summary, "Hamilton-Jacobi-Bellman Power of Two Comparison", dimension_order=[[4, 15, 100], [5, 16, 128]])

In [299]:
df = allen_summary[allen_summary["iteration"] == 4000]
pivot = df.pivot(index='dimension', columns='method', values='mean')
pivot['improvement'] = pivot['brownian'] / pivot['hadamard']
pivot[['brownian','hadamard','improvement']]

method     brownian  hadamard  improvement
dimension                                 
1          0.000154  0.000012    12.802866
2          0.000275  0.000028     9.705069
15         0.000427  0.000235     1.816685
100        0.000165  0.000138     1.195088

In [302]:
df = hjb_summary[hjb_summary["iteration"] == 2000]
pivot = df.pivot(index='dimension', columns='method', values='mean')
pivot['improvement'] = pivot['brownian'] / pivot['hadamard']
pivot[['brownian','hadamard','improvement']]

method     brownian  hadamard  improvement
dimension                                 
1          0.029704  0.006002     4.949161
2          0.043788  0.009633     4.545861
4          0.043302  0.010184     4.251935
5          0.041150  0.017021     2.417535
15         0.046536  0.032305     1.440517
16         0.046034  0.032266     1.426718
100        0.021430  0.006812     3.145888
128        0.017003  0.002163     7.862665

# Testing

In [167]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Dummy data
x = np.linspace(0, 10, 100)
df = pd.DataFrame({
    "run1": np.sin(x) + 1.5*np.random.randn(len(x)),
    "run2": np.sin(x) + 0.1*np.random.randn(len(x)),
    "run3": np.sin(x) + 0.3*np.random.randn(len(x)),
    "run4": np.sin(x) + 0.1*np.random.randn(len(x)),
}, index=x)

# Compute mean and std
mean = df.mean(axis=1)
std = df.std(axis=1)
upper = mean + std
lower = mean - std


In [250]:
# --- Load the data ---
# Assume the first three are "original", next three are "changed"
files_original = ["../cir/Brownian_401_loss_data.npy", "../cir/Brownian_402_loss_data.npy", "../cir/Brownian_403_loss_data.npy"]
files_changed = ["../cir/Step_size_401_loss_data.npy", "../cir/Step_size_402_loss_data.npy", "../cir/Step_size_403_loss_data.npy"]

data = {}
for label, files in zip(["brownian", "hadamard"], [files_original, files_changed]):
    runs = [np.load(f) for f in files]  # each run: array of shape (num_iterations,)
    runs = np.array(runs)  # shape (num_runs, num_iterations)
    mean = runs.mean(axis=0)
    std = runs.std(axis=0)
    data[label] = pd.DataFrame({
        "iteration": np.arange(1, len(mean)+1),
        "mean": mean,
        "std": std,
        "method": label
    })

# Combine into a single DataFrame
summary_df = pd.concat(data.values(), ignore_index=True)

# --- Plotting ---
method_colors = {"brownian": "blue", "hadamard": "red"}

fig = go.Figure()

for method in summary_df["method"].unique():
    df_m = summary_df[summary_df["method"] == method]
    color = method_colors.get(method, "black")

    # Mean line
    fig.add_trace(go.Scatter(
        x=df_m["iteration"],
        y=df_m["mean"],
        mode="lines",
        name=method,
        line=dict(color=color, width=2)
    ))

    # Shaded ±1 SD
    fig.add_trace(go.Scatter(
        x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
        y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
        fill="toself",
        fillcolor=with_alpha(color, 0.2),
        line=dict(color="rgba(255,255,255,0)"),
        showlegend=False,
        hoverinfo="skip"
    ))

fig.update_layout(
    title="CIR Example",
    xaxis_title="Iteration",
    yaxis_title="Loss",
    yaxis_type="log",
    height=600,
    width=650,
)

fig.show()


In [303]:
# --- Load the data ---
# Assume the first three are "original", next three are "changed"
files_original = ["../multi_cir/Brownian_1_loss_data.npy", "../multi_cir/Brownian_2_loss_data.npy", "../multi_cir/Brownian_3_loss_data.npy"]
files_changed = ["../multi_cir/Step_size_1_loss_data.npy", "../multi_cir/Step_size_2_loss_data.npy", "../multi_cir/Step_size_3_loss_data.npy"]

data = {}
for label, files in zip(["brownian", "hadamard"], [files_original, files_changed]):
    runs = [np.load(f) for f in files]  # each run: array of shape (num_iterations,)
    runs = np.array(runs)  # shape (num_runs, num_iterations)
    mean = runs.mean(axis=0)
    std = runs.std(axis=0)
    data[label] = pd.DataFrame({
        "iteration": np.arange(1, len(mean)+1),
        "mean": mean,
        "std": std,
        "method": label
    })

# Combine into a single DataFrame
summary_df = pd.concat(data.values(), ignore_index=True)

# --- Plotting ---
method_colors = {"brownian": "blue", "hadamard": "red"}

fig = go.Figure()

for method in summary_df["method"].unique():
    df_m = summary_df[summary_df["method"] == method]
    color = method_colors.get(method, "black")

    # Mean line
    fig.add_trace(go.Scatter(
        x=df_m["iteration"],
        y=df_m["mean"],
        mode="lines",
        name=method,
        line=dict(color=color, width=2)
    ))

    # Shaded ±1 SD
    fig.add_trace(go.Scatter(
        x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
        y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
        fill="toself",
        fillcolor=with_alpha(color, 0.2),
        line=dict(color="rgba(255,255,255,0)"),
        showlegend=False,
        hoverinfo="skip"
    ))

fig.update_layout(
    title="10D CIR Example",
    xaxis_title="Iteration",
    yaxis_title="Loss",
    yaxis_type="log",
    height=600,
    width=650,
)

fig.show()


In [290]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def with_alpha(color_name, alpha=0.2):
    import matplotlib.colors as mcolors
    rgb = mcolors.to_rgb(color_name)
    r, g, b = [int(255*x) for x in rgb]
    return f'rgba({r},{g},{b},{alpha})'

def prepare_summary(files, label):
    """Load runs from .npy files and return a DataFrame with mean/std per iteration."""
    runs = [np.load(f) for f in files]
    runs = np.array(runs)
    mean = runs.mean(axis=0)
    std = runs.std(axis=0)
    return pd.DataFrame({
        "iteration": np.arange(1, len(mean)+1),
        "mean": mean,
        "std": std,
        "method": label
    })

# --- Data for Experiment 1 ---
files_orig_1 = ["../cir/Brownian_401_loss_data.npy", "../cir/Brownian_402_loss_data.npy", "../cir/Brownian_403_loss_data.npy"]
files_new_1 = ["../cir/Step_size_401_loss_data.npy", "../cir/Step_size_402_loss_data.npy", "../cir/Step_size_403_loss_data.npy"]
summary1 = pd.concat([prepare_summary(files_orig_1, "brownian"),
                      prepare_summary(files_new_1, "hadamard")], ignore_index=True)

# --- Data for Experiment 2 ---
files_orig_2 = ["../multi_cir/Brownian_1_loss_data.npy", "../multi_cir/Brownian_2_loss_data.npy", "../multi_cir/Brownian_3_loss_data.npy"]
files_new_2 = ["../multi_cir/Step_size_1_loss_data.npy", "../multi_cir/Step_size_2_loss_data.npy", "../multi_cir/Step_size_3_loss_data.npy"]

summary2 = pd.concat([prepare_summary(files_orig_2, "brownian"),
                      prepare_summary(files_new_2, "hadamard")], ignore_index=True)

method_colors = {"brownian": "blue", "hadamard": "red"}

# --- Create side-by-side subplots ---
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=["d = 1", "d = 10"]
)

# Plot experiment 1
for method in summary1["method"].unique():
    df_m = summary1[summary1["method"] == method]
    color = method_colors.get(method, "black")

    fig.add_trace(go.Scatter(
        x=df_m["iteration"],
        y=df_m["mean"],
        mode="lines",
        name=method.title(),
        line=dict(color=color, width=2),
        showlegend=True
    ), row=1, col=1)

    fig.add_trace(go.Scatter(
        x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
        y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
        fill="toself",
        fillcolor=with_alpha(color, 0.2),
        line=dict(color="rgba(255,255,255,0)"),
        showlegend=False,
        hoverinfo="skip"
    ), row=1, col=1)

# Plot experiment 2
for method in summary2["method"].unique():
    df_m = summary2[summary2["method"] == method]
    color = method_colors.get(method, "black")

    fig.add_trace(go.Scatter(
        x=df_m["iteration"],
        y=df_m["mean"],
        mode="lines",
        name=method,
        line=dict(color=color, width=2),
        showlegend=False  # only show legend once
    ), row=1, col=2)

    fig.add_trace(go.Scatter(
        x=list(df_m["iteration"]) + list(df_m["iteration"])[::-1],
        y=list(df_m["mean"] - df_m["std"]) + list(df_m["mean"] + df_m["std"])[::-1],
        fill="toself",
        fillcolor=with_alpha(color, 0.2),
        line=dict(color="rgba(255,255,255,0)"),
        showlegend=False,
        hoverinfo="skip"
    ), row=1, col=2)

# Update axes and layout
for i in [1,2]:
    fig.update_xaxes(title_text="Iteration", row=1, col=i)
    fig.update_yaxes(title_text="Loss", type="log", row=1, col=i, tickformat=".0e")

fig.update_layout(
    title="Cox-Ingersoll-Ross Example",
    width=1000,
    height=500
)

fig.show()


In [311]:
df1 = summary1[summary1["iteration"] == 3000].copy()
df1["dimension"] = 1

In [312]:
df2 = summary2[summary2["iteration"] == 3000].copy()
df2["dimension"] = 10

In [316]:
df = pd.concat([df1, df2])
df.head()

iteration      mean       std    method  dimension
2999       3000  0.000512  0.000041  brownian          1
5999       3000  0.000196  0.000023  hadamard          1
2999       3000  0.000768  0.000533  brownian         10
5999       3000  0.000246  0.000178  hadamard         10

In [317]:
pivot = df.pivot(index="dimension", columns="method", values="mean").reset_index()
# Optional: calculate improvement (Brownian / Hadamard)
pivot["improvement"] = pivot["brownian"] / pivot["hadamard"]

In [318]:
pivot

method  dimension  brownian  hadamard  improvement
0               1  0.000512  0.000196     2.613683
1              10  0.000768  0.000246     3.123088